In [96]:
from __future__ import print_function

from keras.models import Sequential, Model
from keras.layers.embeddings import Embedding
from keras.layers import Input, Activation, Dense, Permute, Dropout, add, dot,merge, concatenate
from keras.layers import LSTM
from keras.utils.data_utils import get_file
from keras.preprocessing.sequence import pad_sequences
from functools import reduce
import tarfile
import numpy as np
import re

In [97]:
def tokenize(sent):
    # splitting the sentences based on spaces and tokenizing them
    return [x.strip() for x in re.split('(\W+)?', sent) if x.strip()]



In [98]:
def parse_stories(lines, only_supporting=False):
   
    # Trying to retrive the questions and 
    # ansers to the particular questions
    
    data = []
    story = []
    for line in lines:
        line = line.decode('utf-8').strip()
        nid, line = line.split(' ', 1)
        nid = int(nid)
        if nid == 1:
            story = []
        if '\t' in line:
            q, a, supporting = line.split('\t')
            q = tokenize(q)
            substory = None
            if only_supporting:
                # Only select the related substory
                supporting = map(int, supporting.split())
                substory = [story[i - 1] for i in supporting]
            else:
                # Provide all the substories
                substory = [x for x in story if x]
            data.append((substory, q, a))
            story.append('')
        else:
            sent = tokenize(line)
            story.append(sent)
        
    return data


In [99]:
def get_stories(f, only_supporting=False, max_length=None):
    
    # Discaring the stories longer than the max length defined 
    # and converting the lines in to a single story corresponding 
    # to the questions
    data = parse_stories(f.readlines(), only_supporting=only_supporting)
    flatten = lambda data: reduce(lambda x, y: x + y, data)
    data = [(flatten(story), q, answer) for story, q, answer in data if not max_length or len(flatten(story)) < max_length]
    return data


In [100]:
def vectorize_stories(data, word_idx, story_maxlen, query_maxlen):

    # Mapping the length of stories against story with maximum
    # length and doing necessary padding
    
    X = []
    Xq = []
    Y = []
    for story, query, answer in data:
        x=[word_idx[w] for w in story]
        xq=[word_idx[w] for w in query]
        y=np.zeros(len(word_idx) + 1)
        y[word_idx[answer]]=1
        X.append(x)
        Xq.append(xq)
        Y.append(y)
    return (pad_sequences(X, maxlen=story_maxlen),
            pad_sequences(Xq, maxlen=query_maxlen),
            np.array(Y))


In [101]:
''' Accessing the particula modules of the 
Babi dataset saperated by the modules
'''

try:
    path = get_file('babi-tasks-v1-2.tar.gz', origin='https://s3.amazonaws.com/text-datasets/babi_tasks_1-20_v1-2.tar.gz')
except:
    print('Error downloading dataset, please download it manually:\n'
          '$ wget http://www.thespermwhale.com/jaseweston/babi/tasks_1-20_v1-2.tar.gz\n'
          '$ mv tasks_1-20_v1-2.tar.gz ~/.keras/datasets/babi-tasks-v1-2.tar.gz')
    raise
tar = tarfile.open(path)


In [102]:
challenges = {'qa6_yes-no-questions': 'tasks_1-20_v1-2/en-10k/qa6_yes-no-questions_{}.txt'}
challenge_type = 'qa6_yes-no-questions'
challenge = challenges[challenge_type]

print('Extracting stories for the challenge:', challenge_type)
train_stories = get_stories(tar.extractfile(challenge.format('train')))
test_stories = get_stories(tar.extractfile(challenge.format('test')))

Extracting stories for the challenge: qa6_yes-no-questions


/usr/lib/python3.5/re.py:203: FutureWarning: split() requires a non-empty pattern match.
  return _compile(pattern, flags).split(string, maxsplit)


In [103]:
print(train_stories)

[(['Mary', 'moved', 'to', 'the', 'bathroom', '.', 'Sandra', 'journeyed', 'to', 'the', 'bedroom', '.'], ['Is', 'Sandra', 'in', 'the', 'hallway', '?'], 'no'), (['Mary', 'moved', 'to', 'the', 'bathroom', '.', 'Sandra', 'journeyed', 'to', 'the', 'bedroom', '.', 'Mary', 'went', 'back', 'to', 'the', 'bedroom', '.', 'Daniel', 'went', 'back', 'to', 'the', 'hallway', '.'], ['Is', 'Daniel', 'in', 'the', 'bathroom', '?'], 'no'), (['Mary', 'moved', 'to', 'the', 'bathroom', '.', 'Sandra', 'journeyed', 'to', 'the', 'bedroom', '.', 'Mary', 'went', 'back', 'to', 'the', 'bedroom', '.', 'Daniel', 'went', 'back', 'to', 'the', 'hallway', '.', 'Sandra', 'went', 'to', 'the', 'kitchen', '.', 'Daniel', 'went', 'back', 'to', 'the', 'bathroom', '.'], ['Is', 'Daniel', 'in', 'the', 'office', '?'], 'no'), (['Mary', 'moved', 'to', 'the', 'bathroom', '.', 'Sandra', 'journeyed', 'to', 'the', 'bedroom', '.', 'Mary', 'went', 'back', 'to', 'the', 'bedroom', '.', 'Daniel', 'went', 'back', 'to', 'the', 'hallway', '.', 'Sa

In [104]:
print(test_stories)

[(['Mary', 'got', 'the', 'milk', 'there', '.', 'John', 'moved', 'to', 'the', 'bedroom', '.'], ['Is', 'John', 'in', 'the', 'kitchen', '?'], 'no'), (['Mary', 'got', 'the', 'milk', 'there', '.', 'John', 'moved', 'to', 'the', 'bedroom', '.', 'Mary', 'discarded', 'the', 'milk', '.', 'John', 'went', 'to', 'the', 'garden', '.'], ['Is', 'John', 'in', 'the', 'kitchen', '?'], 'no'), (['Mary', 'got', 'the', 'milk', 'there', '.', 'John', 'moved', 'to', 'the', 'bedroom', '.', 'Mary', 'discarded', 'the', 'milk', '.', 'John', 'went', 'to', 'the', 'garden', '.', 'Daniel', 'moved', 'to', 'the', 'bedroom', '.', 'Daniel', 'went', 'to', 'the', 'garden', '.'], ['Is', 'John', 'in', 'the', 'garden', '?'], 'yes'), (['Mary', 'got', 'the', 'milk', 'there', '.', 'John', 'moved', 'to', 'the', 'bedroom', '.', 'Mary', 'discarded', 'the', 'milk', '.', 'John', 'went', 'to', 'the', 'garden', '.', 'Daniel', 'moved', 'to', 'the', 'bedroom', '.', 'Daniel', 'went', 'to', 'the', 'garden', '.', 'Daniel', 'travelled', 'to', 

In [105]:
vocab = set()
for story, q, answer in train_stories + test_stories:
    print(story)
    vocab |= set(story + q + [answer])
vocab = sorted(vocab)

# Reserve 0 for masking via pad_sequences
vocab_size = len(vocab) + 1
story_maxlen = max(map(len, (x for x, _, _ in train_stories + test_stories)))
query_maxlen = max(map(len, (x for _, x, _ in train_stories + test_stories)))

['Mary', 'moved', 'to', 'the', 'bathroom', '.', 'Sandra', 'journeyed', 'to', 'the', 'bedroom', '.']
['Mary', 'moved', 'to', 'the', 'bathroom', '.', 'Sandra', 'journeyed', 'to', 'the', 'bedroom', '.', 'Mary', 'went', 'back', 'to', 'the', 'bedroom', '.', 'Daniel', 'went', 'back', 'to', 'the', 'hallway', '.']
['Mary', 'moved', 'to', 'the', 'bathroom', '.', 'Sandra', 'journeyed', 'to', 'the', 'bedroom', '.', 'Mary', 'went', 'back', 'to', 'the', 'bedroom', '.', 'Daniel', 'went', 'back', 'to', 'the', 'hallway', '.', 'Sandra', 'went', 'to', 'the', 'kitchen', '.', 'Daniel', 'went', 'back', 'to', 'the', 'bathroom', '.']
['Mary', 'moved', 'to', 'the', 'bathroom', '.', 'Sandra', 'journeyed', 'to', 'the', 'bedroom', '.', 'Mary', 'went', 'back', 'to', 'the', 'bedroom', '.', 'Daniel', 'went', 'back', 'to', 'the', 'hallway', '.', 'Sandra', 'went', 'to', 'the', 'kitchen', '.', 'Daniel', 'went', 'back', 'to', 'the', 'bathroom', '.', 'Daniel', 'picked', 'up', 'the', 'football', 'there', '.', 'Daniel', '

['Mary', 'travelled', 'to', 'the', 'bedroom', '.', 'John', 'got', 'the', 'milk', 'there', '.', 'Mary', 'journeyed', 'to', 'the', 'garden', '.', 'Sandra', 'went', 'back', 'to', 'the', 'bathroom', '.', 'Sandra', 'travelled', 'to', 'the', 'hallway', '.', 'Sandra', 'travelled', 'to', 'the', 'bedroom', '.', 'Sandra', 'went', 'to', 'the', 'bathroom', '.', 'Sandra', 'moved', 'to', 'the', 'office', '.']
['Mary', 'travelled', 'to', 'the', 'bedroom', '.', 'John', 'got', 'the', 'milk', 'there', '.', 'Mary', 'journeyed', 'to', 'the', 'garden', '.', 'Sandra', 'went', 'back', 'to', 'the', 'bathroom', '.', 'Sandra', 'travelled', 'to', 'the', 'hallway', '.', 'Sandra', 'travelled', 'to', 'the', 'bedroom', '.', 'Sandra', 'went', 'to', 'the', 'bathroom', '.', 'Sandra', 'moved', 'to', 'the', 'office', '.', 'Daniel', 'went', 'back', 'to', 'the', 'bathroom', '.', 'Daniel', 'picked', 'up', 'the', 'apple', 'there', '.']
['John', 'picked', 'up', 'the', 'apple', 'there', '.', 'John', 'dropped', 'the', 'apple', 

['Daniel', 'moved', 'to', 'the', 'office', '.', 'Daniel', 'went', 'back', 'to', 'the', 'garden', '.', 'Daniel', 'took', 'the', 'football', 'there', '.', 'John', 'went', 'to', 'the', 'garden', '.', 'John', 'picked', 'up', 'the', 'milk', 'there', '.', 'Mary', 'went', 'to', 'the', 'hallway', '.', 'John', 'put', 'down', 'the', 'milk', '.', 'Mary', 'moved', 'to', 'the', 'kitchen', '.', 'Mary', 'went', 'to', 'the', 'hallway', '.', 'Daniel', 'picked', 'up', 'the', 'milk', 'there', '.']
['Mary', 'grabbed', 'the', 'football', 'there', '.', 'Mary', 'dropped', 'the', 'football', '.', 'Daniel', 'travelled', 'to', 'the', 'bathroom', '.', 'Daniel', 'travelled', 'to', 'the', 'office', '.']
['Mary', 'grabbed', 'the', 'football', 'there', '.', 'Mary', 'dropped', 'the', 'football', '.', 'Daniel', 'travelled', 'to', 'the', 'bathroom', '.', 'Daniel', 'travelled', 'to', 'the', 'office', '.', 'Mary', 'went', 'back', 'to', 'the', 'hallway', '.', 'Mary', 'went', 'back', 'to', 'the', 'office', '.']
['Mary', 'g

['Daniel', 'journeyed', 'to', 'the', 'hallway', '.', 'John', 'moved', 'to', 'the', 'office', '.', 'John', 'picked', 'up', 'the', 'milk', 'there', '.', 'John', 'left', 'the', 'milk', '.', 'Sandra', 'journeyed', 'to', 'the', 'bathroom', '.', 'Sandra', 'went', 'to', 'the', 'hallway', '.', 'Daniel', 'journeyed', 'to', 'the', 'kitchen', '.', 'Sandra', 'went', 'to', 'the', 'office', '.']
['Daniel', 'journeyed', 'to', 'the', 'hallway', '.', 'John', 'moved', 'to', 'the', 'office', '.', 'John', 'picked', 'up', 'the', 'milk', 'there', '.', 'John', 'left', 'the', 'milk', '.', 'Sandra', 'journeyed', 'to', 'the', 'bathroom', '.', 'Sandra', 'went', 'to', 'the', 'hallway', '.', 'Daniel', 'journeyed', 'to', 'the', 'kitchen', '.', 'Sandra', 'went', 'to', 'the', 'office', '.', 'Daniel', 'moved', 'to', 'the', 'garden', '.', 'Daniel', 'moved', 'to', 'the', 'office', '.']
['Mary', 'journeyed', 'to', 'the', 'bedroom', '.', 'Daniel', 'moved', 'to', 'the', 'kitchen', '.']
['Mary', 'journeyed', 'to', 'the', 'b

In [106]:
with open('story_maxlen_yes-no-questions.txt','w') as file:
    file.write(str(story_maxlen))
    file.write('\n')
file.close()


with open('query_maxlen_yes-no-questions.txt','w') as file:
    file.write(str(query_maxlen))
    file.write('\n')
file.close()


In [107]:
''' Knowing some facts and stats about the 
module of dataset we are using
'''

print('-')
print('Vocab size:', vocab_size, 'unique words')
print('Story max length:', story_maxlen, 'words')
print('Query max length:', query_maxlen, 'words')
print('Number of training stories:', len(train_stories))
print('Number of test stories:', len(test_stories))
print('-')
print('Here\'s what a "story" tuple looks like (input, query, answer):')
print(train_stories[0])
print('-')
print('Vectorizing the word sequences...')

word_idx = dict((c, i + 1) for i, c in enumerate(vocab))
idx_word = dict((i+1, c) for i,c in enumerate(vocab))
inputs_train, queries_train, answers_train = vectorize_stories(train_stories,
                                                               word_idx,
                                                               story_maxlen,
                                                               query_maxlen)
inputs_test, queries_test, answers_test = vectorize_stories(test_stories,
                                                            word_idx,
                                                            story_maxlen,
                                                            query_maxlen)

-
Vocab size: 38 unique words
Story max length: 156 words
Query max length: 6 words
Number of training stories: 10000
Number of test stories: 1000
-
Here's what a "story" tuple looks like (input, query, answer):
(['Mary', 'moved', 'to', 'the', 'bathroom', '.', 'Sandra', 'journeyed', 'to', 'the', 'bedroom', '.'], ['Is', 'Sandra', 'in', 'the', 'hallway', '?'], 'no')
-
Vectorizing the word sequences...


In [108]:
with open('word_idx_yes-no-questions.txt','w') as file:
    file.write(str(word_idx))
file.close()

In [109]:
with open('idx_word_yes-no-questions.txt','w') as file:
    file.write(str(idx_word))
file.close()

In [110]:
print(word_idx)

{'bedroom': 11, 'back': 9, 'Sandra': 7, 'John': 5, 'hallway': 19, 'the': 30, 'picked': 28, 'to': 32, 'Daniel': 3, 'journeyed': 21, 'dropped': 14, 'left': 23, 'Is': 4, 'there': 31, 'bathroom': 10, 'apple': 8, 'down': 13, 'up': 35, 'office': 27, '.': 1, 'garden': 16, 'grabbed': 18, 'went': 36, 'in': 20, 'travelled': 34, 'football': 15, 'took': 33, 'kitchen': 22, 'no': 26, 'discarded': 12, 'moved': 25, 'got': 17, 'milk': 24, '?': 2, 'put': 29, 'Mary': 6, 'yes': 37}


In [111]:
print(idx_word)

{1: '.', 2: '?', 3: 'Daniel', 4: 'Is', 5: 'John', 6: 'Mary', 7: 'Sandra', 8: 'apple', 9: 'back', 10: 'bathroom', 11: 'bedroom', 12: 'discarded', 13: 'down', 14: 'dropped', 15: 'football', 16: 'garden', 17: 'got', 18: 'grabbed', 19: 'hallway', 20: 'in', 21: 'journeyed', 22: 'kitchen', 23: 'left', 24: 'milk', 25: 'moved', 26: 'no', 27: 'office', 28: 'picked', 29: 'put', 30: 'the', 31: 'there', 32: 'to', 33: 'took', 34: 'travelled', 35: 'up', 36: 'went', 37: 'yes'}


In [112]:
print('-')
print('inputs: integer tensor of shape (samples, max_length)')
print('inputs_train shape:', inputs_train.shape)
print('inputs_test shape:', inputs_test.shape)
print('-')
print('queries: integer tensor of shape (samples, max_length)')
print('queries_train shape:', queries_train.shape)
print('queries_test shape:', queries_test.shape)
print('-')
print('answers: binary (1 or 0) tensor of shape (samples, vocab_size)')
print('answers_train shape:', answers_train.shape)
print('answers_test shape:', answers_test.shape)
print('-')
print('Compiling...')

-
inputs: integer tensor of shape (samples, max_length)
inputs_train shape: (10000, 156)
inputs_test shape: (1000, 156)
-
queries: integer tensor of shape (samples, max_length)
queries_train shape: (10000, 6)
queries_test shape: (1000, 6)
-
answers: binary (1 or 0) tensor of shape (samples, vocab_size)
answers_train shape: (10000, 38)
answers_test shape: (1000, 38)
-
Compiling...


In [113]:
train_epochs = 120
batch_size = 32
lstm_size = 64

In [114]:
# initiating 
input_sequence = Input((story_maxlen,))
question = Input((query_maxlen,))

print('Input sequence:', input_sequence)
print('Question:', question)

# defining the encoder for the input and embedding the vocab
input_encoder_m = Sequential()
input_encoder_m.add(Embedding(input_dim=vocab_size,
                              output_dim=64))
input_encoder_m.add(Dropout(0.3))

# mapping the dimensions according to the maximum length on input
input_encoder_c = Sequential()
input_encoder_c.add(Embedding(input_dim=vocab_size,
                              output_dim=query_maxlen))
input_encoder_c.add(Dropout(0.3))

# vectorizing the questions
question_encoder = Sequential()
question_encoder.add(Embedding(input_dim=vocab_size,
                               output_dim=64,
                               input_length=query_maxlen))
question_encoder.add(Dropout(0.3))


# conctinating input stories and questions
input_encoded_m = input_encoder_m(input_sequence)
print('Input encoded m', input_encoded_m)
input_encoded_c = input_encoder_c(input_sequence)
print('Input encoded c', input_encoded_c)
question_encoded = question_encoder(question)
print('Question encoded', question_encoded)


# cross refrencing the questions against the stories
match = merge([input_encoded_m, question_encoded], mode='dot', dot_axes=(2, 2))
print(match.shape)
match = Activation('softmax')(match)
print('Match shape', match)

response = merge([match, input_encoded_c], mode='sum')
response = Permute((2, 1))(response)  
print('Response shape', response)

# mapping answers against the vector of question and stories
answer = merge([response, question_encoded], mode='concat')
print('Answer shape', answer)

answer = LSTM(64)(answer)  
answer = Dropout(0.3)(answer)
answer = Dense(vocab_size)(answer)  

# popping out prob. of answers
answer = Activation('softmax')(answer)

Input sequence: Tensor("input_7:0", shape=(?, 156), dtype=float32)
Question: Tensor("input_8:0", shape=(?, 6), dtype=float32)
Input encoded m Tensor("sequential_19/dropout_13/cond/Merge:0", shape=(?, 156, 64), dtype=float32)
Input encoded c Tensor("sequential_20/dropout_14/cond/Merge:0", shape=(?, 156, 6), dtype=float32)
Question encoded Tensor("sequential_21/dropout_15/cond/Merge:0", shape=(?, 6, 64), dtype=float32)
(?, 156, 6)
Match shape Tensor("activation_7/truediv:0", shape=(?, 156, 6), dtype=float32)
Response shape Tensor("permute_4/transpose:0", shape=(?, 6, 156), dtype=float32)
Answer shape Tensor("merge_12/concat:0", shape=(?, 6, 220), dtype=float32)


/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:38: UserWarning: The `merge` function is deprecated and will be removed after 08/2017. Use instead layers from `keras.layers.merge`, e.g. `add`, `concatenate`, etc.
/home/ubuntu/src/keras/keras/legacy/layers.py:464: UserWarning: The `Merge` layer is deprecated and will be removed after 08/2017. Use instead layers from `keras.layers.merge`, e.g. `add`, `concatenate`, etc.
  name=name)
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:43: UserWarning: The `merge` function is deprecated and will be removed after 08/2017. Use instead layers from `keras.layers.merge`, e.g. `add`, `concatenate`, etc.
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:48: UserWarning: The `merge` function is deprecated and will be removed after 08/2017. Use instead layers from `keras.layers.merge`, e.g. `add`, `concatenate`, etc.


In [115]:
model = Model([input_sequence, question], answer)
model.compile(optimizer='rmsprop', loss='categorical_crossentropy',
              metrics=['accuracy'])

In [116]:
model.fit([inputs_train, queries_train], answers_train, batch_size, train_epochs,
          validation_data=([inputs_test, queries_test], answers_test))

Train on 10000 samples, validate on 1000 samples
Epoch 1/120
10000/10000 [==============================] - 5s 535us/step - loss: 0.7840 - acc: 0.4978 - val_loss: 0.6940 - val_acc: 0.5030
Epoch 2/120
10000/10000 [==============================] - 5s 462us/step - loss: 0.7011 - acc: 0.4973 - val_loss: 0.6952 - val_acc: 0.4970
Epoch 3/120
10000/10000 [==============================] - 5s 461us/step - loss: 0.6966 - acc: 0.4946 - val_loss: 0.6955 - val_acc: 0.4970
Epoch 4/120
10000/10000 [==============================] - 5s 461us/step - loss: 0.6949 - acc: 0.5045 - val_loss: 0.6943 - val_acc: 0.4970
Epoch 5/120
10000/10000 [==============================] - 5s 457us/step - loss: 0.6943 - acc: 0.5030 - val_loss: 0.6960 - val_acc: 0.4970
Epoch 6/120
10000/10000 [==============================] - 5s 456us/step - loss: 0.6929 - acc: 0.5152 - val_loss: 0.7077 - val_acc: 0.5030
Epoch 7/120
10000/10000 [==============================] - 5s 459us/step - loss: 0.6934 - acc: 0.5117 - val_loss: 0.6

10000/10000 [==============================] - 5s 453us/step - loss: 0.1105 - acc: 0.9578 - val_loss: 0.8049 - val_acc: 0.8130
Epoch 118/120
10000/10000 [==============================] - 5s 454us/step - loss: 0.1116 - acc: 0.9586 - val_loss: 0.8283 - val_acc: 0.8190
Epoch 119/120
10000/10000 [==============================] - 5s 454us/step - loss: 0.1103 - acc: 0.9571 - val_loss: 0.8035 - val_acc: 0.8260
Epoch 120/120
10000/10000 [==============================] - 5s 454us/step - loss: 0.1100 - acc: 0.9578 - val_loss: 0.8586 - val_acc: 0.8210


In [117]:
''' Getting the feel for the test dataset
and how it is devided.
'''

' Getting the feel for the test dataset\nand how it is devided.\n'

In [118]:
for i in range(0,10):
        current_inp = test_stories[i]
        current_story, current_query, current_answer = vectorize_stories([current_inp], word_idx, story_maxlen, query_maxlen)
        current_prediction = model.predict([current_story, current_query])
        current_prediction = idx_word[np.argmax(current_prediction)]
        print(' '.join(current_inp[0]), ' '.join(current_inp[1]), '| Prediction:', current_prediction, '| Ground Truth:', current_inp[2])
        print("-----------------------------------------------------------------------------------------")
        

Mary got the milk there . John moved to the bedroom . Is John in the kitchen ? | Prediction: no | Ground Truth: no
-----------------------------------------------------------------------------------------
Mary got the milk there . John moved to the bedroom . Mary discarded the milk . John went to the garden . Is John in the kitchen ? | Prediction: no | Ground Truth: no
-----------------------------------------------------------------------------------------
Mary got the milk there . John moved to the bedroom . Mary discarded the milk . John went to the garden . Daniel moved to the bedroom . Daniel went to the garden . Is John in the garden ? | Prediction: yes | Ground Truth: yes
-----------------------------------------------------------------------------------------
Mary got the milk there . John moved to the bedroom . Mary discarded the milk . John went to the garden . Daniel moved to the bedroom . Daniel went to the garden . Daniel travelled to the bathroom . Sandra travelled to the

In [119]:
print(story)

['Mary', 'moved', 'to', 'the', 'kitchen', '.', 'Mary', 'travelled', 'to', 'the', 'office', '.', 'Daniel', 'picked', 'up', 'the', 'milk', 'there', '.', 'Sandra', 'went', 'to', 'the', 'garden', '.', 'Sandra', 'grabbed', 'the', 'apple', 'there', '.', 'Sandra', 'dropped', 'the', 'apple', '.', 'Daniel', 'dropped', 'the', 'milk', '.', 'Mary', 'went', 'to', 'the', 'garden', '.', 'Daniel', 'took', 'the', 'milk', 'there', '.', 'Mary', 'picked', 'up', 'the', 'apple', 'there', '.']


In [120]:
from keras.models import model_from_json
model_json = model.to_json()
with open("model_yes-no-questions.json", "w") as json_file:
    json_file.write(model_json)
# serialize weights to HDF5
model.save_weights("model_yes-no-questions.h5")
print("Saved model to disk")

Saved model to disk


In [121]:
json_file = open('model_yes-no-questions.json', 'r')
loaded_model_json = json_file.read()
json_file.close()
loaded_model = model_from_json(loaded_model_json)
# load weights into new model
loaded_model.load_weights("model_yes-no-questions.h5")

/home/ubuntu/src/keras/keras/engine/topology.py:1269: UserWarning: The `Merge` layer is deprecated and will be removed after 08/2017. Use instead layers from `keras.layers.merge`, e.g. `add`, `concatenate`, etc.
  return cls(**config)


In [122]:
test_stories[0]

(['Mary',
  'got',
  'the',
  'milk',
  'there',
  '.',
  'John',
  'moved',
  'to',
  'the',
  'bedroom',
  '.'],
 ['Is', 'John', 'in', 'the', 'kitchen', '?'],
 'no')

In [123]:
loaded_model.compile(optimizer='rmsprop', loss='categorical_crossentropy',
              metrics=['accuracy'])
for i in range(0,10):
        current_inp = test_stories[i]
        current_story, current_query, current_answer = vectorize_stories([current_inp], word_idx, story_maxlen, query_maxlen)
        current_prediction = loaded_model.predict([current_story, current_query])
        current_prediction = idx_word[np.argmax(current_prediction)]
        print(' '.join(current_inp[0]), ' '.join(current_inp[1]), '| Prediction:', current_prediction, '| Ground Truth:', current_inp[2])
        print("-----------------------------------------------------------------------------------------")


Mary got the milk there . John moved to the bedroom . Is John in the kitchen ? | Prediction: no | Ground Truth: no
-----------------------------------------------------------------------------------------
Mary got the milk there . John moved to the bedroom . Mary discarded the milk . John went to the garden . Is John in the kitchen ? | Prediction: no | Ground Truth: no
-----------------------------------------------------------------------------------------
Mary got the milk there . John moved to the bedroom . Mary discarded the milk . John went to the garden . Daniel moved to the bedroom . Daniel went to the garden . Is John in the garden ? | Prediction: yes | Ground Truth: yes
-----------------------------------------------------------------------------------------
Mary got the milk there . John moved to the bedroom . Mary discarded the milk . John went to the garden . Daniel moved to the bedroom . Daniel went to the garden . Daniel travelled to the bathroom . Sandra travelled to the

In [124]:
print(current_story)

[[ 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
   0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
   0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
   0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  3 36
   9 32 30 22  1  6 18 30  8 31  1  3 21 32 30 27  1  5 36  9 32 30 27  1
   6 23 30  8  1  3 36 32 30 19  1  5 36 32 30 19  1  3 28 35 30 24 31  1
   5 18 30 15 31  1  6 17 30  8 31  1]]


In [125]:
print(current_query)

[[ 4  3 20 30 19  2]]


In [126]:
print(len(current_query))

1


In [127]:
print(test_stories[0])

(['Mary', 'got', 'the', 'milk', 'there', '.', 'John', 'moved', 'to', 'the', 'bedroom', '.'], ['Is', 'John', 'in', 'the', 'kitchen', '?'], 'no')
